In [8]:
from pyspark.sql import SparkSession

# Create a DataFrame using SparkSession
spark = (SparkSession
    .builder
    .appName("data_cleaning")
    .enableHiveSupport()
    .getOrCreate())

In [ ]:
# Sorry i seriouly don't know why i have to do this
import pandas as pd

pandas_df = pd.read_json('/home/jazzdung/E-Commerce-Support-System/mr_clean/shopee.ndjson', lines=True)
df = spark.createDataFrame(pandas_df) 

# # File location and type
# file_location = "/home/jazzdung/Projects/E-Commerce-Support-System/mr_clean/shopee.ndjson"
# file_type = "json"

# # CSV options
# infer_schema = "false"
# first_row_is_header = "true"
# delimiter = ","

# # The applied options are for CSV files. For other file types, these will be ignored.
# df = spark.read.format(file_type) \
#   .option("inferSchema", infer_schema) \
#     .option("mode", "failFast")\
#     .option("multiline", "true")\
#     .load(file_location)
# #   .option("header", first_row_is_header) \
# #   .option("sep", delimiter) \
# #   .load(file_location)

# df.show(100, truncate=False)

In [10]:
df.printSchema()

root
 |-- product_name: string (nullable = true)
 |-- price: string (nullable = true)
 |-- product_desc: string (nullable = true)
 |-- avg_rating: double (nullable = true)
 |-- num_review: string (nullable = true)
 |-- num_sold: string (nullable = true)
 |-- attrs: map (nullable = true)
 |    |-- key: string
 |    |-- value: string (valueContainsNull = true)
 |-- url: string (nullable = true)



**Chú ý: với các data dạng string, cần bỏ các kí tự đặc biệt (chỉ dữ lại chữ + số)**

**Tên sp**
- Dùng regex để lọc và bỏ những cái string có thể leak giá ra ngoài)
- Lowercase + bỏ kí tự đặc biệt

In [11]:
from pyspark.sql.functions import udf
import pyspark.sql.functions as f
import re

# Lowercase
def lower_case(s):
    return s.lower()

# Remove Yeu thich, Yeu thich+
def remove_liked_product(s):
    s = re.sub('yêu thích\n', '', s)
    s = re.sub('yêu thích\+\n', '', s)
    return s

# Remove contents inside [], option indicate promotion, prices    
def remove_between_square_brackets(s):
    s = re.sub(r'\[.*?\]', '', s)
    return s

# Remove special character
def remove_special_character(s):
    s = re.sub('[^A-Za-z0-9 ]+', ' ', s)
    s = re.sub(' +', ' ', s)
    return s

# Remove vietnamese character
def no_accent_vietnamese(s):
    s = re.sub(r'[àáạảãâầấậẩẫăằắặẳẵ]', 'a', s)
    s = re.sub(r'[èéẹẻẽêềếệểễ]', 'e', s)
    s = re.sub(r'[òóọỏõôồốộổỗơờớợởỡ]', 'o', s)
    s = re.sub(r'[ìíịỉĩ]', 'i', s)
    s = re.sub(r'[ùúụủũưừứựửữ]', 'u', s)
    s = re.sub(r'[ỳýỵỷỹ]', 'y', s)
    s = re.sub(r'[đ]', 'd', s)
    return s

# Remove redundant spaces
def remove_spaces(s):
    s = s.lstrip()
    return s

# Bundled up
def clean_product_name(name):
    name = lower_case(name)
    name = remove_liked_product(name)
    name = remove_between_square_brackets(name)
    name = no_accent_vietnamese(name)
    name = remove_special_character(name)
    name = remove_spaces(name)

    return name

udf_clean_product_name = udf(clean_product_name)

df.withColumn("product_name", udf_clean_product_name(df["product_name"])).select("product_name").show(10, truncate=False)


+----------------------------------------------------------+
|product_name                                              |
+----------------------------------------------------------+
|ao khoac cardigan vien xanh nau frmlk form rong chew      |
|ao khoac cardigan vien xanh nau frmlk form rong chew      |
|ao len tam co 3 phan ao len tam ao len tam hang quang chau|
|ao len tam co 3 phan ao len tam ao len tam hang quang chau|
|ao len tam co 3 phan ao len tam ao len tam hang quang chau|
|ao len tam co 3 phan ao len tam ao len tam hang quang chau|
|ao len tam co 3 phan ao len tam ao len tam hang quang chau|
|ao len tam co 3 phan ao len tam ao len tam hang quang chau|
|ao len tam co 3 phan ao len tam ao len tam hang quang chau|
|ao len tam co 3 phan ao len tam ao len tam hang quang chau|
+----------------------------------------------------------+
only showing top 10 rows



**Giá sp**
- Bỏ chữ “đ" (đ55.000)

In [12]:
# 50.000đ -> 50.000
def remove_dong(s):
    s = re.sub('₫', '', s)
    return s

# 50.000 -> 50000
def remove_dot(s):
    s = re.sub('\.', '', s)
    return s

# ₫48.000 - ₫59.000 -> ₫48.000
def remove_second_price (s):
    s = s.split('-')[0]
    s = re.sub(' ', '', s)
    return s

def clean_price(s):
    s = remove_dong(s)
    s = remove_dot(s)
    s = remove_second_price(s)
    return s

udf_clean_price = udf(clean_price)

df.withColumn("price", udf_clean_price(df["price"])).select("price").show(10, truncate=False)

+------+
|price |
+------+
|      |
|110000|
|48000 |
|59000 |
|59000 |
|59000 |
|59000 |
|59000 |
|59000 |
|59000 |
+------+
only showing top 10 rows



**Chi tiết sp (dạng String)**
- Phải bỏ html
- Dùng regex để lọc và bỏ những cái string có thể leak giá ra ngoài)
- Lowercase + bỏ kí tự đặc biệt

In [13]:
# Make the description somehow readable

def clean_desc(s):
    s = re.sub(' &amp;', ' &', s)
    s = re.sub('<svg.*?</svg>', '', s)
    s = re.sub('<div>', '', s)   
    s = re.sub('div', '', s)

    # Group lables into 1 row
    s = re.sub('</a>', '-', s)  

    s = re.sub('</label>', ': ', s)

    s = re.sub('class=', '', s)
    s = re.sub('"', '', s)
    s = re.sub('< ', '<', s)    
    s = re.sub("\/.*?\>","/>", s)

    # Delete redundant texts, spaces
    s = re.sub('<label.*?>', '', s)
    s = re.sub('<flex.*?>', '', s)
    s = re.sub(' href=/', '', s)
    s = re.sub('<a ', '<', s)
    s = re.sub('<p ', '<', s)
    s = re.sub(' +', ' ', s)



    # s = re.sub('</svg>', '', s)
    # s = re.sub('</path>', '', s)
    # s = re.sub('<svg.*?>', '', s)
    # s = re.sub('<path.*?>', '', s)

    #Split
    s = re.sub('</>', '/', s)
    s = re.sub('<.*?>', '', s)
    s = s.split("/")
    s = [x for x in s if x!= '']

    return s

desc = df.first()['product_desc']


# print(desc)

for x in clean_desc(desc):
    print(x)

udf_clean_desc = udf(clean_desc)

df.withColumn("new_product_desc", udf_clean_desc(df["product_desc"])).select("new_product_desc").show(1000, truncate=False)

CHI TIẾT SẢN PHẨM
Danh Mục: Shopee-Thời Trang Nữ-Áo len & Cardigan-
Chiều dài tay áo: Dài tay
Kho hàng: 8817
Gửi từ: Hà Nội
MÔ TẢ SẢN PHẨM
Áo Khoác Cardigan Viền Xanh Nâu FRMLK Form Rộng
 - Form: Freesize, 65-75kg đổ lại mặc oke 
- Kích thước: Dài 65cm (xem trên ảnh thứ 2 của sản phẩm)
- Phân loại: Be viền xanh, Be viền nâu
 - Chất liệu: Nỉ Bông 
#cardigan #cardigannamnu #cardiganformrong #aocardigan #aokhoac #nasumay


+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [14]:
# Get country
def get_country(s):
    desc_list = clean_desc(s)
    truncate_index = desc_list.index('MÔ TẢ SẢN PHẨM')
    desc_list = desc_list[:truncate_index]
    country = ""
    for x in desc_list:
        if "Xuất xứ" in x:
            country = re.sub('.*?: ', '', x)

    return country

# Get brand
def get_brand(s):
    desc_list = clean_desc(s)
    truncate_index = desc_list.index('MÔ TẢ SẢN PHẨM')
    desc_list = desc_list[:truncate_index]
    brand = ""
    for x in desc_list:
            if "Thương hiệu" in x:
                brand = re.sub('.*?: ', '', x)

    return brand[:-1]

# get_brand("/svg><a class=\"akCPfg KvmvO1\" href=\"/Áo-len-Cardigan-cat.11035639.11035672\">Áo len &amp; Cardigan</a></div></div><div class=\"dR8kXc\"><label class=\"zquA4o\">Thương hiệu</label><a class=\"GvvZVe\" href=\"/search?brands=3358741\">porozi</a></div><div class=\"dR8kXc\"><label class=\"zquA4o\">Chiều dài tay áo</label><div>Dài tay</div></div><div class=\"dR8kXc\"><label class=\"zquA4o\">Phong cách</label><div>Thể thao, Cơ bản, Hàn Quốc, Tối giản, Retro</div></div><div class=\"dR8kXc\"><label class=\"zquA4o\">Chiều dài áo khoác ngoài</label><div>Ngắn</div></div><div class=\"dR8kXc\"><label class=\"zquA4o\">Chất liệu</label><div>Đan</div></div><div class=\"dR8kXc\"><label class=\"zquA4o\">Mùa</label><div>Mùa thu</div></div><div class=\"dR8kXc\"><label class=\"zquA4o\">Rất lớn</label><div>Không</div></div><div class=\"dR8kXc\"><label class=\"zquA4o\">Petite</label><div>Có</div></div><div class=\"dR8kXc\"><label class=\"zquA4o\">Xuất xứ</label><div>Trung Quốc</div></div><div class=\"dR8kXc\"><label class=\"zquA4o\">Mẫu</label><div>Khác</div></div><div class=\"dR8kXc\"><label class=\"zquA4o\">Kho hàng</label><div>19960</div></div><div class=\"dR8kXc\"><label class=\"zquA4o\">Gửi từ</label><div>Nước ngoài</div></div></div></div><div class=\"U9rGd1\"><div class=\"Iv7FJp\">MÔ TẢ SẢN PHẨM</div><div class=\"MCCLkq\"><div class=\"f7AU53\"><p class=\"irIKAp\">10.23</p><p class=\"irIKAp\">\n</p><p class=\"irIKAp\">【Fo Hội nghị ony, không có tiêu chuẩn thực tế】</p><p class=\"irIKAp\">\n</p><p class=\"irIKAp\">Kích THƯỚC · Chiều dài 47 cm Ngực 88 cm Tay áo 56 cm</p><p class=\"irIKAp\">\n</p><p class=\"irIKAp\">\n</p><p class=\"irIKAp\">(Đơn Vị: cm. Đo kích thước bằng tay khi lát gạch, có thể có sai số 2-3 cm, chỉ để tham khảo)</p><p class=\"irIKAp\">\n</p><p class=\"irIKAp\">Ghi chú:</p><p class=\"irIKAp\">Đơn vị tính: cm</p><p class=\"irIKAp\">\tVì hiệu ứng hiển thị và ánh sáng khác nhau, màu sắc thực tế của sản phẩm có thể hơi khác so với màu sắc trong hình. Cảm ơn bạn.</p><p class=\"irIKAp\">\tNếu sản phẩm của chúng tôi không có kích thước hay màu sắc yêu thích của bạn, hoặc bạn muốn tìm hiểu thêm thông tin, vui lòng liên hệ với chúng tôi. Cảm ơn bạn.</p><p class=\"irIKAp\">\tNếu có vấn đề gì khi nhận gói hàng, xin hãy liên hệ với chúng tôi để được hỗ trợ xử lý, chúng tôi sẽ giải đáp thỏa đáng cho bạn.</p><p class=\"irIKAp\">\tTất cả các sản phẩm đều được gửi về từ nước ngoài, chất lượng siêu tốt với mức giá rẻ, các bạn thấy thích thì đừng quên chia sẻ cho bạn bè mình nha!</p><div class=\"irIKAp\"><div style=\"position: relative; width: 100%; padding-bottom: 133.333%;\"><div class=\"nUpNF8\" style=\"position: absolute; left: 0px; right: 0px; width: 100%; height: 100%;\"><img class=\"_0O7Vlf Zro+rB\"><div class=\"N+wPR-\"><div class=\"nvwfJv\"></div></div></div></div></div><div class=\"irIKAp\"><div s")

udf_get_country = udf(get_country)
udf_get_brand= udf(get_brand)

df.withColumn("country", udf_get_country(df["product_desc"])).select("country").show(1000, truncate=False)
df.withColumn("brand", udf_get_brand(df["product_desc"])).select("brand").show(1000, truncate=False)

+----------+
|country   |
+----------+
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |
|          |

In [15]:
# Get stock
def get_specific_desc(s, type):
    desc_list = clean_desc(s)

    # Remove everything after 'MÔ TẢ SẢN PHẨM'
    truncate_index = desc_list.index('MÔ TẢ SẢN PHẨM')
    desc_list = desc_list[:truncate_index]

    value = ""
    for x in desc_list:
        if type in x:
            value = re.sub('.*?: ', '', x)
            value = value.split("-")
    
    return value


get_specific_desc(desc, 'Kho hàng')
get_specific_desc(desc, 'Gửi từ')


['Hà Nội']

In [16]:
# Get description inside of description, god forbid these naming
def get_smaller_desc_list(s):
    desc_list = clean_desc(s)

    # GET everything after 'MÔ TẢ SẢN PHẨM'
    truncate_index = desc_list.index('MÔ TẢ SẢN PHẨM')
    desc_list = desc_list[truncate_index+1:]

    if len(desc_list) == 1:
        desc_list = ''.join(desc_list)
        return desc_list 
    else:
        desc_list = ' \n '.join(desc_list)
        return desc_list 

get_smaller_desc_list(desc)

'Áo Khoác Cardigan Viền Xanh Nâu FRMLK Form Rộng\n - Form: Freesize, 65-75kg đổ lại mặc oke \n- Kích thước: Dài 65cm (xem trên ảnh thứ 2 của sản phẩm)\n- Phân loại: Be viền xanh, Be viền nâu\n - Chất liệu: Nỉ Bông \n#cardigan #cardigannamnu #cardiganformrong #aocardigan #aokhoac #nasumay'

**category**    
- Phân category ra làm 3 tầng, sẽ có 3 attribute là cat1,cat2, cat3
- cat2 có format là :”cat1 / cat2”, cat3 là “cat1 / cat2 / cat3

In [17]:
# Get category

def get_category_list(s):
    desc_list = clean_desc(s)
    cat = desc_list[1]
    cat = re.sub('.*?: ', '', cat)
    cat = cat[:-1]
    cat = cat.split("-")

    # Remove shopee
    cat = cat[1:]
    
    return cat

def first_cat(s):
    cat_list = get_category_list(s)
    
    if len(cat_list) >= 1:
        cat = cat_list[0]
    else:
        cat = ""
    
    return cat


def second_cat(s):
    cat_list = get_category_list(s)
    
    if len(cat_list) >= 2:
        cat = cat_list[0] + " / " + cat_list[1]
    else:
        cat = ""
    
    return cat

def third_cat(s):
    cat_list = get_category_list(s)
    
    if len(cat_list) >= 3:
        cat = cat_list[0] + " / " + cat_list[1] + " / " + cat_list[2]
    else:
        cat = ""
    
    return cat

udf_first_cat = udf(first_cat)
udf_second_cat = udf(second_cat)
udf_third_cat = udf(third_cat)


print(first_cat(desc))
print(second_cat(desc))
print(third_cat(desc))


Thời Trang Nữ
Thời Trang Nữ / Áo len & Cardigan



In [18]:
# Test with different type of product
pandas_df_socks = pd.read_json('/home/jazzdung/E-Commerce-Support-System/mr_clean/shopee_socks.ndjson', lines=True)
df_socks = spark.createDataFrame(pandas_df_socks) 

desc = df_socks.first()['product_desc']

# print(desc)
print(clean_desc(desc))

# df_socks.withColumn("new_product_desc", udf_clean_desc(df["product_desc"])).select("new_product_desc").show(1000, truncate=False)

['CHI TIẾT SẢN PHẨM', 'Danh Mục: Shopee-Thời Trang Nữ-Vớ', '>Khác-', 'Xuất xứ: Nhật Bản', 'Kho hàng: 5914', 'Gửi từ: Nước ngoài', 'MÔ TẢ SẢN PHẨM', 'Chất liệu: sợi acrylic', 'Chiều dài: 70cm, 50cm, 40cm', 'Có thể kéo qua đầu gối', 'Cách giặt: giặt tay bằng nước lạnh, không giặt máy, giặt khô & tẩy trắng, phơi khô.', 'Có 2-3 cm sự khác biệt theo phép đo thủ công', 'Bạn sẽ nhận được: 1 Đôi']


/home/jazzdung/.local/lib/python3.10/site-packages/pyspark/sql/pandas/conversion.py:474: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for column, series in pdf.iteritems():
/home/jazzdung/.local/lib/python3.10/site-packages/pyspark/sql/pandas/conversion.py:486: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for column, series in pdf.iteritems():


**Số đánh giá**
- 3,2k -> 3200

In [19]:
# 3,2k -> 3200

def k_to_number(s):
    if "," in s:
        s = re.sub(',', '', s)
        s = re.sub('k', '00', s)
    else:
        s = re.sub('k', '000', s)
    
    return s

udf_clean_num_review = udf(k_to_number)

df.withColumn("num_review", udf_clean_num_review(df["num_review"])).select("num_review").show(10, truncate=False)

# df = df.withColumn("num_review", udf_clean_num_review(df["num_review"])).select("num_review")
# df = df.withColumn("num_sold", udf_clean_num_review(df["num_sold"])).select("num_sold")

+----------+
|num_review|
+----------+
|3200      |
|3200      |
|1000      |
|1000      |
|1000      |
|1000      |
|1000      |
|1000      |
|1000      |
|1000      |
+----------+
only showing top 10 rows



**Shop info**

In [20]:
pd_new_product = pd.read_json('/home/jazzdung/E-Commerce-Support-System/mr_clean/new_product.ndjson', lines=True)
df_new_data = spark.createDataFrame(pd_new_product) 

/home/jazzdung/.local/lib/python3.10/site-packages/pyspark/sql/pandas/conversion.py:474: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for column, series in pdf.iteritems():
/home/jazzdung/.local/lib/python3.10/site-packages/pyspark/sql/pandas/conversion.py:486: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for column, series in pdf.iteritems():


In [21]:
info = df_new_data.first()['shop_info']

def get_shop_info_list(s):
    list = s.split("\n")

    return list

# udf_get_shop_info_list = udf(get_shop_info_list)
# df_new_data.withColumn("new_info", udf_clean_num_review(df_new_data["shop_info"])).select("new_info").show(100, truncate=False)


get_shop_info_list(info)

['Yêu Thích+',
 'shopphukiencuoigiang',
 'Online 1 Phút Trước',
 'Chat Ngay',
 'Xem Shop',
 'Đánh Giá',
 '51,7k',
 'Sản Phẩm',
 '2k',
 'Tỉ Lệ Phản Hồi',
 '96%',
 'Thời Gian Phản Hồi',
 'trong vài giờ',
 'Tham Gia',
 '6 năm trước',
 'Người Theo Dõi',
 '93,4k']

In [22]:
# Get liked shop

def liked_shop(s):
    info_list = s.split("\n")

    if info_list[0] == "Yêu Thích+":
        tier = 2
    elif info_list[0] == "Yêu Thích":
        tier = 1
    else:
        tier = 0
    return tier

udf_liked_shop= udf(liked_shop)
# df_new_data.withColumn("shop_liked_tier", udf_liked_shop(df_new_data["shop_info"])).select("shop_liked_tier").show(10, truncate=False)

In [23]:
# Get amount of shop's reviews

def get_shop_num_review(s):
    info_list = s.split("\n")
    
    index = info_list.index('Đánh Giá')
    value = info_list[index+1]
    value = k_to_number(value)
    
    return value

udf_get_shop_num_review = udf(get_shop_num_review)
# df_new_data.withColumn("shop_num_review", udf_get_shop_num_review(df_new_data["shop_info"])).select("shop_num_review").show(10, truncate=False)

In [24]:
# Get amount of shop product

def get_shop_num_product(s):
    info_list = s.split("\n")
    
    index = info_list.index('Sản Phẩm')
    value = info_list[index+1]
    value = k_to_number(value)
    
    return value

udf_get_shop_num_product= udf(get_shop_num_product)
# df_new_data.withColumn("shop_num_product", udf_get_shop_num_product(df_new_data["shop_info"])).select("shop_num_product").show(100, truncate=False)

In [25]:
# Get reply percentages

def get_reply_percentage(s):
    info_list = s.split("\n")
    
    index = info_list.index('Tỉ Lệ Phản Hồi')
    value = info_list[index+1]
    value = float(value.strip('%'))/100
    
    return value

udf_get_reply_percentage= udf(get_reply_percentage)
# df_new_data.withColumn("reply_percentage", udf_get_reply_percentage(df_new_data["shop_info"])).select("reply_percentage").show(100, truncate=False)

In [26]:
# Get reply time

def get_reply_time(s):
    info_list = s.split("\n")
    
    index = info_list.index('Thời Gian Phản Hồi')
    value = info_list[index+1]
    
    return value

udf_get_reply_time= udf(get_reply_time)
# df_new_data.withColumn("reply_time", udf_get_reply_time(df_new_data["shop_info"])).select("reply_time").show(100, truncate=False)

In [27]:
# Get shop creation time

def normalize_date(s):

    # Get the number
    num = s.split(" ")[0]

    if "năm" in s:
        num = str(int(num)*12)
    elif "tháng" in s:
        num = num
    else:
        num = 0
    return num

def get_shop_creation_time(s):
    info_list = s.split("\n")
    
    index = info_list.index('Tham Gia')
    value = info_list[index+1]
    value = normalize_date(value)

    return value

udf_get_shop_creation_time= udf(get_shop_creation_time)
# df_new_data.withColumn("shop_creation_time", udf_get_shop_creation_time(df_new_data["shop_info"])).select("shop_creation_time").show(100, truncate=False)

In [28]:

# Get amount of shop follower

def get_shop_num_follower(s):
    info_list = s.split("\n")
    
    index = info_list.index('Người Theo Dõi')
    value = info_list[index+1]
    value = k_to_number(value)
    
    return value

udf_get_shop_num_follower= udf(get_shop_num_follower)
df_new_data.withColumn("shop_num_follower", udf_get_shop_num_follower(df_new_data["shop_info"])).select("shop_num_follower").show(100, truncate=False)


+-----------------+
|shop_num_follower|
+-----------------+
|93400            |
|93400            |
|93400            |
|19100            |
|19100            |
|19100            |
|19100            |
|19100            |
|19100            |
|19100            |
|19100            |
|19100            |
|19100            |
|19100            |
|19100            |
|19100            |
|19100            |
|19100            |
|19100            |
|19100            |
|19100            |
|24100            |
|13400            |
|1600             |
|1600             |
|1600             |
|1600             |
|1600             |
|1600             |
|1600             |
|1600             |
|1600             |
|1600             |
|1600             |
|1600             |
|1600             |
|1600             |
+-----------------+



**Shipping**

In [32]:
def clean_shipping(s):
    s = re.sub('null', '', s)
    return s

udf_clean_shipping = udf(clean_shipping)

# Assembles!

In [31]:
pd_new_product = pd.read_json('/home/jazzdung/E-Commerce-Support-System/mr_clean/new_product.ndjson', lines=True)
df_new_data = spark.createDataFrame(pd_new_product) 

df_new_data.show(1000, truncate = False)

df_cleaned = df_new_data.withColumn("shop_num_follower", udf_get_shop_num_follower(df_new_data["shop_info"])).select("shop_num_follower").show(100, truncate=False)


/home/jazzdung/.local/lib/python3.10/site-packages/pyspark/sql/pandas/conversion.py:474: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for column, series in pdf.iteritems():
/home/jazzdung/.local/lib/python3.10/site-packages/pyspark/sql/pandas/conversion.py:486: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for column, series in pdf.iteritems():


+----------------------------------------------------------------------------------------------------------------------------------+---------------------------------------------+-----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+--------+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------